# Using Sympy tensor package in general relativity

This notebook tries to introduce the use of Sympy tensor package for computations in general relativity. It is assumed that the user has a foundation in general relativity, and is somewhat familiar with Sympy (there are already nice tutorials for that). The aim of this notebook is to present some of the basic tools to help a user to progress from scratch to practical tensor calculations in general relativity. All calculations are carried out explicitly, without recourse to any extra functions defined on top of Sympy. The idea is that based on the given examples, a user can then develop her/his own code for the problems at hand. The current version of the notebook uses Sympy 1.13. 

© Laur Järv, Roald Ivask, Joosep Lember, Reelika Pärnpuu, Hanna Liis Tamm, University of Tartu, laur.jarv@ut.ee, 04.07.2025

## Getting started

### Initialize

First must import Sympy core and its tensor package. Then a nice display capability of formulae is also useful.

In [ ]:
# Import useful packages
from sympy import *
import sympy.tensor.tensor as sympytensor
from sympy.tensor.toperators import PartialDerivative

# Nice display of formulae
from IPython.display import Latex, Math
init_printing()

In [ ]:
# On a wide high resolution screen, use the display to full width (width:100%), or reserve left margin for table of contents (e.g. width:85%)
#from IPython.display import display, HTML
#display(HTML("<style>:root { --jp-notebook-max-width: 90% !important; margin-left:10%;}</style>"))
#display(HTML("<style>.jp-Cell {margin-left:-500px; width: 2200px !important; }</style>"))

### Basic operations

Sympy tensor package aims to treat tensors at two levels. 
+ The first level is with abstract indexes where definitions and computations are valid in for any spacetime and coordinate system. 
+ The second is the explicit component level, where tensors are evaluated for a particular spacetime and coordinate system as arrays of data.

In [ ]:
# Define spacetime indices 
ST = sympytensor.TensorIndexType('SpaceTime', dummy_name='iota', dim=4, metric_symmetry=1)
mu, nu, rho, sigma, alpha, beta, gamma = sympytensor.tensor_indices('\\mu, \\nu, \\rho, \\sigma, \\alpha, \\beta, \\gamma', ST)

# Define some tensor heads
coord = sympytensor.TensorHead('x', [ST]) # coordinates
metric = sympytensor.TensorHead('g', [ST]*2) # metric
diff_metric = sympytensor.TensorHead('\\partial g', [ST]*3) # partial derivatives of the metric

In [ ]:
# Introduce spherical coordinates:
r = symbols('r', positive=True)
t, theta, phi = symbols('t, \\theta, \\phi', real=True)

coord_spherical = [t,r,theta,phi]

Tensor objects data is stored in the format of _ImmutableDenseNDimArray_. 

In [ ]:
# Define the metric, row by row
metric_spherical_ll = ImmutableDenseNDimArray([[-1, 0, 0, 0],[0,1,0,0],[0,0,r**2,0],[0,0,0,r**2*sin(theta)**2]])
display(Math('g_{\\mu \\nu}' + '=' + latex(metric_spherical_ll) ))

In [ ]:
# To compute the inverse of the metric, first convert it into a matrix, then invert, then back to 
metric_spherical_uu = ImmutableDenseNDimArray(Matrix(metric_spherical_ll).inv())
display(Math('g^{\\mu \\nu}' + '=' + latex(metric_spherical_uu)))

Use tensor addition, multiplication, and contraction to define abstract tensor formulae. Indices with minus are lower, without a minus upper. Rational(1,2) keeps Sympy from translating 1/2 to 0.5. Note that above we defined omega to be the name for dummy indices.

In [ ]:
# Use tensor addition and multiplication to define abstract tensor formulae: -mu means lower spacetime index "mu", mu means upper spacetime index "mu"
metric_symmetrized_ll=Rational(1,2)*(metric(-mu,-nu)+metric(-nu,-mu))
display(Math('g_{(\\mu \\nu)}' + '=' + latex(metric_symmetrized_ll)))

metric_antisymmetrized_ll=Rational(1,2)*(metric(-mu,-nu)-metric(-nu,-mu))
display(Math('g_{[\\mu \\nu]}' + '=' + latex(metric_antisymmetrized_ll)))

metric_contracted_lu=(metric(-mu,-alpha)*metric(alpha,nu))
display(Math('g_{\\mu}{}^{\\nu}' + '=' + latex(metric_contracted_lu)))

In [ ]:
# Once the abstract definitions are in place, the components are evaluated by .replace_with_arrays: in the place of g(-mu,-nu) substitute the components of g_spherical_ll
metricsym_spherical_ll=metric_symmetrized_ll.replace_with_arrays({metric(-mu,-nu): metric_spherical_ll})
display(Math('g_{(\\mu \\nu)}' + '=' + latex(metricsym_spherical_ll)))

metricasym_spherical_ll=metric_antisymmetrized_ll.replace_with_arrays({metric(-mu,-nu): metric_spherical_ll})
display(Math('g_{[\\mu \\nu]}' + '=' + latex(metricasym_spherical_ll)))

In [ ]:
# Sympy can do index raising and lowering automatically, must specify the type of the index (here ST) and the covatiant metric
metriccontracted_spherical_lu=metric_contracted_lu.replace_with_arrays({ST: metric_spherical_ll, metric(mu,nu): metric_spherical_uu})
display(Math('\\delta_\\mu^\\nu = g_{\\mu}{}^{\\nu}' + '=' + latex(metriccontracted_spherical_lu)))

In the current version of Sympy (1.13) some simple operations can be done on the purely abstract level, without evaluating the components in specific coordinates. But these capabilites are still very limited.

In [ ]:
# Define a metric contraction
metric_contracted_=metric(-mu,-nu)*metric(mu,nu)
display(metric_contracted_)

In [ ]:
# Execute the abstract computation
metric_contracted_.contract_metric(metric)

To apply some operation to all the components, can use the *.applyfunc lambda* method. The *.applyfunc(simplify)* also works directly.

In [ ]:
# Here lambda defines an operation applying to all the elements (items)
metric_sphericalcos_ll=metric_spherical_ll.applyfunc(lambda item: item.subs(sin(theta)**2,1-cos(theta)**2))
display(Math('g_{\\mu \\nu}' + '=' + latex(metric_sphericalcos_ll) ))

In [ ]:
# .applyfunc(simplify) works directly
metric_sphericalsin_ll=metric_sphericalcos_ll.applyfunc(simplify)
display(Math('g_{\\mu \\nu}' + '=' + latex(metric_sphericalsin_ll) ))

Can call out a particular components and do operations with them. Remember that in Python the first component has index value 0.

In [ ]:
# Let's play
A=metric_spherical_ll[0,0]-1/metric_spherical_uu[2,2]+metric_spherical_ll[3,3]
display(A)
display(A.simplify())
display(A.factor())
display(A.collect(r))
display(A.collect(r,simplify))
display(A.collect(r,factor))
display(A.collect(r,factor).expand())

To manipulate only one tensor component and substitute the result back to the tensor, it is possible to convert the immutable array structure into a mutable array, do the manipulations, and convert back to an immutable array.

In [ ]:
# Immutable array is immune to changes, but mutable array components can be redefined
A=MutableDenseNDimArray(metric_sphericalsin_ll)
A[3,3]=A[3,3].subs(sin(theta)**2,1-cos(theta)**2)
A[3,3]
metric_sphericalcos_ll=ImmutableDenseNDimArray(A)
display(metric_sphericalcos_ll)

Can print out the formulae in latex. Super useful!

In [ ]:
# Print the latex of the metrix
print(latex(metric_spherical_ll))

### Caveats

One bothersome issue is that in the abstract tensor definitions Sympy follows some alphabetic rules to order the terms, and reads out the order of indices from that alphabetic order of the terms. The unnatural order of terms is harmless, but the unnatural order of indices can be confusing and easily lead to mistakes. A solution is to introduce a tensor of zeroes which is put to the first place among the terms, and thus sets the desired index ordering. 

In [ ]:
# Define the heads of connection, its partial derivatives, and curvature
Connection = sympytensor.TensorHead('\\Gamma', [ST]*3) # general connection
diff_Connection = sympytensor.TensorHead('\\partial \\Gamma', [ST]*4) # derivatives of the general connection
Riemann = sympytensor.TensorHead('R', [ST]*4) # general Riemann curvature tensor

In [ ]:
# Naive definition of the curvature tensor
Riemann_ulll=diff_Connection(alpha,-nu,-beta,-mu)-diff_Connection(alpha,-mu,-beta,-nu)+Connection(alpha,-mu,-gamma)*Connection(gamma,-nu,-beta)-Connection(alpha,-nu,-gamma)*Connection(gamma,-mu,-beta)
display(Math('R^{\\alpha}{}_{\\beta\\mu\\nu}' + '=' + latex(Riemann_ulll)))
display(Riemann_ulll.get_free_indices())
print('but we want the order of the middle indices reversed')

In [ ]:
# A trick to manipulate the order of indices in tensor definitions
Set_indices4 = sympytensor.TensorHead('', [ST]*4) # zero object to set the order of indices right

# Better definition of the curvature tensor
Riemann_ulll=-Set_indices4(alpha,-beta,-mu,-nu)+diff_Connection(alpha,-nu,-beta,-mu)-diff_Connection(alpha,-mu,-beta,-nu)+Connection(alpha,-mu,-gamma)*Connection(gamma,-nu,-beta)-Connection(alpha,-nu,-gamma)*Connection(gamma,-mu,-beta)
display(Math('R^{\\alpha}{}_{\\beta\\mu\\nu}' + '=' + latex(Riemann_ulll)))
display(Riemann_ulll.get_free_indices())
print('note the empty headless term in the middle')

Another minor issue is that the word *lambda* has a special meaning in Python as a function. On the other hand it would be nice to mechanically copy abstract tensor formulae from books and papers where the index lambda comes up quite ofter. The solution is to introduce index *lembda* which is printed as $\lambda$.

In [ ]:
lembda = sympytensor.tensor_indices('\\lambda', ST)

### Einstein's equations for spatially flat Friedmann cosmology

To avoid confuison from random names, we will adopt the following legend for abstract tensor definitions, valid for any spacetime and coordinate system: *TensorHeadName_IndicesUpperOrLower*. For example: 

+ *metric_ll* covariant components of a metric
+ *Riemann_ulll* components of a Riemann tensor in the usual order upper-lower-lower-lower.

Once again, *metric(-mu,-nu)* denotes tensor g with lower indices, while *metric(mu,nu)* with upper indices.

In [ ]:
# Some more tensor heads, that have not been defined before

Ricci = sympytensor.TensorHead('R', [ST]*2) # Ricci tensor
R = symbols('R') # curvature scalar
Einstein = sympytensor.TensorHead('G', [ST]*2) # Einstein tensor
EMT = sympytensor.TensorHead('T', [ST]*2) # matter energy-momentum tensor

# Some more spacetime indices, like the Greek letters
st0, st1, st2, st3, st4 = sympytensor.tensor_indices('st0:5', ST)

# Tensor definitions, from the beginning

diff_metric_lll=PartialDerivative(metric(-mu,-nu),coord(rho))
display(Math('\\partial g_{\\mu \\nu, \\rho}' + '=' + latex(diff_metric_lll)))
display(diff_metric_lll.get_free_indices())

Connection_ull=Rational(1,2)*metric(lembda,rho)*(diff_metric(-nu,-rho,-mu)+diff_metric(-rho,-mu,-nu)-diff_metric(-mu,-nu,-rho))
display(Math('\\Gamma^{\\lambda}{}_{\\mu\\nu}' + '=' + latex(Connection_ull)))
display(Connection_ull.get_free_indices())

diff_Connection_ulll=PartialDerivative(Connection(lembda,-mu,-nu),coord(rho))
display(Math('\\partial \\Gamma{}^{\\lambda}{}_{\\mu\\nu , \\rho}' + '=' + latex(diff_Connection_ulll)))
display(diff_Connection_ulll.get_free_indices())

Riemann_ulll=-Set_indices4(alpha,-beta,-mu,-nu)+diff_Connection(alpha,-nu,-beta,-mu)-diff_Connection(alpha,-mu,-beta,-nu)+Connection(alpha,-mu,-gamma)*Connection(gamma,-nu,-beta)-Connection(alpha,-nu,-gamma)*Connection(gamma,-mu,-beta)
display(Math('R^{\\alpha}{}_{\\beta\\mu\\nu}' + '=' + latex(Riemann_ulll)))
display(Riemann_ulll.get_free_indices())

Ricci_ll=Riemann(rho,-mu,-rho,-nu) 
display(Math('R_{\\mu\\nu}' + '=' + latex(Ricci_ll)))
display(Ricci_ll.get_free_indices())

R_=metric(mu,nu)*Ricci(-mu,-nu) 
display(Math('R' + '=' + latex(R_)))
display(R_.get_free_indices())

Einstein_ll = Ricci(-mu,-nu)-Rational(1,2)*metric(-mu,-nu)*R
display(Math('G_{\\mu\\nu}' + '=' + latex(Einstein_ll)))
display(Einstein_ll.get_free_indices())

# Note that the index of the partial derivative is positioned as the last index.

Above we adopted the following legend for tensor components in particular spacetime in particular coordinates: *TensorHeadName_SpacetimeName_SpacetimeCoordinates_IndicesUpperOrLower*. If one is always working in the same spacetime or in the same coordinates, then for brevity the spacetime name or coordinates specification can be dropped, e.g. the Minkowski space spacetime in Cartesian coordinates. For example:
+ *metric_Mink_ll* covariant components of the Minkowski metric in Cartesian coordinates,
+ *Connection_FLRW_sph_ull* connection coefficients of the Friedmann-Lemaitre-Robertson-Walker metric in spherical coordinates, first index contravariant, two last indexes covariant, 
+ *Riemann_FRLW0_Cart_ulll* components of the Riemann curvature tensor of the spatially flat Friedmann-Lemaitre-Robertson-Walker metric in quasi-Cartesian coordinates, index structure contravariant-covariant-covariant-covariant.

In [ ]:
#Coordinates:
r = Symbol('r',positive=True)
t, theta, phi = symbols('t,theta,phi',real=True)
coord_sph = [t,r,theta,phi]
aa = Function('a', positive=True) # scale factor
a = Symbol('a', positive=True)

# Define metric components
metric_FLRW0_sph_ll = ImmutableDenseNDimArray([[-1, 0, 0, 0],[0,aa(t)**2,0,0],[0,0,aa(t)**2*r**2,0],[0,0,0,aa(t)**2*r**2*sin(theta)**2]])
display(Math('g_{\\mu \\nu}' + '=' + latex(metric_FLRW0_sph_ll)))

Sympy tensor package can handle raising and lowering indices automatically, which can be useful in many contexts like special relativity, or when the metric is rather simple. In this section we will use this possibility. We will store all computed quantities in a list, which can be invoked in any computation that comes next.

In [ ]:
# In this section we store all the computed quantities into a list
tensors_FLRW0_sph = {coord(st0):coord_sph}
tensors_FLRW0_sph.update({ST:metric_FLRW0_sph_ll})
tensors_FLRW0_sph.update({metric(-st0,-st1):metric_FLRW0_sph_ll})

In [ ]:
# Calculate the partial derivatives of the metric: diff_metric_lll was defined above now we substitute in the metric with lower indices and coordinates. 
# To avoid accidental misordering in the substitutions it is better to use the index names st0, st1 and not the Greek letters that we used to define the abstract formulae

diff_metric_FLRW0_sph_lll=diff_metric_lll.replace_with_arrays(tensors_FLRW0_sph, [-st0,-st1,-st2])
tensors_FLRW0_sph.update({diff_metric(-st0,-st1,-st2):diff_metric_FLRW0_sph_lll})

In [ ]:
# Calculate the Levi-Civita connection coefficients:
# ST: g_FLRW0_sph_ll means covariant components of the metric that is used to raise and lower the indices is g_FLRW0_sph_ll
# g(-st0,-st1):g_FLRW0_sph_ll specifies the input metric with lower indices, the procedure will automatically compute the metric with upper indices from it
# dg(-st0,-st1,-st2): dg_FLRW0_sph_lll specifies the partial derivatives

Connection_FLRW0_sph_ull=Connection_ull.replace_with_arrays(tensors_FLRW0_sph, [st0,-st1,-st2]).applyfunc(simplify)
tensors_FLRW0_sph.update({Connection(st0,-st1,-st2):Connection_FLRW0_sph_ull})
display(Math('\\Gamma^{\\rho}{}_{\\mu \\nu}' + '=' + latex(Connection_FLRW0_sph_ull)))

In [ ]:
# Calculate the derivatives of the Levi-Civita connection coefficients
# In this step there is no need to raise or lower indices

diff_Connection_FLRW0_sph_ulll=diff_Connection_ulll.replace_with_arrays(tensors_FLRW0_sph, [st0,-st1,-st2,-st3])
tensors_FLRW0_sph.update({diff_Connection(st0,-st1,-st2,-st3):diff_Connection_FLRW0_sph_ulll})

In [ ]:
# In the next step we need the components of a tensor with only zeros, let us define it here
empty_set={}
empty={}
empty_set=ImmutableSparseNDimArray(empty,(4,4,4,4))
set_indices4=ImmutableDenseNDimArray(empty_set,(4,4,4,4))
tensors_FLRW0_sph.update({Set_indices4(st0,-st1,-st2,-st3):set_indices4})

In [ ]:
# Calculate the components of the Riemann tensor, note we need to insert the emtpy tensor also in the computation

Riemann_FLRW0_sph_ulll=Riemann_ulll.replace_with_arrays(tensors_FLRW0_sph, [st0,-st1,-st2,-st3]).applyfunc(simplify)
tensors_FLRW0_sph.update({Riemann(st0,-st1,-st2,-st3):Riemann_FLRW0_sph_ulll})
display(Math('R^{\\rho}{}_{\\sigma \\mu \\nu}' + '=' + latex(Riemann_FLRW0_sph_ulll))) 

In [ ]:
# Calculate the components of the Ricci tensor
Ricci_FLRW0_sph_ll=Ricci_ll.replace_with_arrays(tensors_FLRW0_sph, [-st0,-st1]).applyfunc(simplify)
tensors_FLRW0_sph.update({Ricci(-st0,-st1):Ricci_FLRW0_sph_ll})
display(Math('R^{\\mu \\nu}' + '=' + latex(Ricci_FLRW0_sph_ll)))

In [ ]:
# Calculate the curvature scalar
R_FLRW0_sph_=R_.replace_with_arrays(tensors_FLRW0_sph, [])
display(Math('R' + '=' + latex(R_FLRW0_sph_)))

In [ ]:
# Calculate the components of the Einstein tensor, note the Ricci scalar is not a tensor, and instead of replace_with_arrays must be simply substituted in

Einstein_FLRW0_sph_ll=Einstein_ll.replace_with_arrays(tensors_FLRW0_sph, [-st0,-st1]).subs(R,R_FLRW0_sph_).applyfunc(simplify)
tensors_FLRW0_sph.update({Einstein(-st0,-st1):Einstein_FLRW0_sph_ll})
display(Math('G^{\\mu \\nu}' + '=' + latex(Einstein_FLRW0_sph_ll)))

In [ ]:
# To substitute in the Hubble function
HH=Function('H', real=True)
a_to_Hubble=[(diff(aa(t),t,t),solve(diff(HH(t),t)-diff(diff(aa(t),t)/aa(t),t),diff(aa(t),t,t))[0]),(diff(aa(t),t),solve(HH(t)-diff(aa(t),t)/aa(t),diff(aa(t),t))[0])]
display(a_to_Hubble)

In [ ]:
# Raise one index and substitute in H
Einstein_FLRW0_sph_ul=Einstein(st0,-st1).replace_with_arrays(tensors_FLRW0_sph, [st0,-st1]).applyfunc(lambda item:item.subs(a_to_Hubble).expand())
display(Math('G^{\\mu}{}_{\\nu}' + '=' + latex(Einstein_FLRW0_sph_ul)))

In [ ]:
# Define the energy-momentum tensor

rr=Function('\\rho', real=True) # matter density
pp=Function('p', real=True) # matter pressure

# Matter energy-momentum
EMT_FLRW0_sph_ll = ImmutableDenseNDimArray(Matrix([[rr(t), 0, 0, 0],[0,aa(t)**2*pp(t),0,0],[0,0,aa(t)**2*r**2*pp(t),0],[0,0,0,aa(t)**2*r**2*sin(theta)**2*pp(t)]]))
tensors_FLRW0_sph.update({EMT(-st0,-st1):EMT_FLRW0_sph_ll})
display(Math('T_{\\mu \\nu}' + '=' + latex(EMT_FLRW0_sph_ll)))

In [ ]:
# Raise the first index
EMT_FLRW0_sph_ul=EMT(st0,-st1).replace_with_arrays(tensors_FLRW0_sph, [st0,-st1])
display(Math('T^{\\mu}{}_{\\nu}' + '=' + latex(EMT_FLRW0_sph_ul)))

In [ ]:
#Friedmann's equations
coupling=Symbol('\\kappa', positive=True) # gravitational coupling

FR0=Eq(-Einstein_FLRW0_sph_ul[0,0],-coupling**2 * EMT_FLRW0_sph_ul[0,0])
FR1=Eq(-Einstein_FLRW0_sph_ul[1,1],-coupling**2 * EMT_FLRW0_sph_ul[1,1])
display(FR0)
display(FR1)

#### Exercises

1) Define the covariant derivative of the metric, and check that it is zero.
2) Define the covariant derivative of the Einstein tensor, and check that it is zero.
3) Define the covariant derivative of the energy-momentum tensor, and check that it gives the continuity equation.

## Basic calculations

### Einstein's equations for curved Friedmann cosmology

When the metric is more involved, rather than computing the raising or lowering of the indices each time again when necessary, it is more efficient to compute it once, and next time use the components from memory. Also, when the same spacetime is represented in different coordinates, we would need to store several lists of computed quantities. In the following in each replace_with_arrays we will call only the quantities necessary in that particular computation. In practice this also works against accidental typos in defining the indices.

In [ ]:
# Define metric components
k=Symbol('k', real=True)

metric_FLRW_sph_ll = ImmutableDenseNDimArray([[-1, 0, 0, 0],[0,aa(t)**2/(1-k*r**2),0,0],[0,0,aa(t)**2*r**2,0],[0,0,0,aa(t)**2*r**2*sin(theta)**2]])
display(Math('g_{\\mu \\nu}' + '=' + latex(metric_FLRW_sph_ll)))

In [ ]:
# Calculate inverse metric
metric_FLRW_sph_uu = ImmutableDenseNDimArray(Matrix(metric_FLRW_sph_ll).inv())
display(Math('g^{\\mu \\nu}' + '=' + latex(metric_FLRW_sph_uu)))

In [ ]:
# Calculate the partial derivatives of the metric
diff_metric_FLRW_sph_lll=diff_metric_lll.replace_with_arrays({metric(-st0,-st1): metric_FLRW_sph_ll, coord(rho): coord_sph})
diff_metric_FLRW_sph_lll

In [ ]:
# Calculate the Levi-Civita connection coefficients
Connection_FLRW_sph_ull=Connection_ull.replace_with_arrays({metric(st0,st1): metric_FLRW_sph_uu, diff_metric(-st0,-st1,-st2): diff_metric_FLRW_sph_lll}).applyfunc(simplify)
display(Math('\\Gamma^{\\rho}{}_{\\mu \\nu}' + '=' + latex(Connection_FLRW_sph_ull)))

In [ ]:
# Calculate the derivatives of the Levi-Civita connection coefficients
diff_Connection_FLRW_sph_ulll=diff_Connection_ulll.replace_with_arrays({Connection(st0,-st1,-st2): Connection_FLRW_sph_ull, coord(rho): coord_sph})
diff_Connection_FLRW_sph_ulll

In [ ]:
# Calculate the components of the Riemann tensor
Riemann_FLRW_sph_ulll=Riemann_ulll.replace_with_arrays({Set_indices4(st0,-st1,-st2,-st3): set_indices4, Connection(st0,-st1,-st2): Connection_FLRW_sph_ull, diff_Connection(st0,-st1,-st2,-st3): diff_Connection_FLRW_sph_ulll}).applyfunc(simplify)
Riemann_FLRW_sph_ulll

In [ ]:
# Calculate the components of the Ricci tensor
Ricci_FLRW_sph_ll=Ricci_ll.replace_with_arrays({Riemann(st0,-st1,-st2,-st3): Riemann_FLRW_sph_ulll}).applyfunc(simplify)
Ricci_FLRW_sph_ll

In [ ]:
# Calculate the curvature scalar
R_FLRW_sph_=R_.replace_with_arrays({metric(st0,st1): metric_FLRW_sph_uu, Ricci(-st0,-st1): Ricci_FLRW_sph_ll})
display(Math('R' + '=' + latex(simplify(R_FLRW_sph_))))

In [ ]:
# Calculate the components of the Einstein tensor
Einstein_FLRW_sph_ll=Einstein_ll.replace_with_arrays({Ricci(-st0,-st1): Ricci_FLRW_sph_ll, metric(-st0,-st1): metric_FLRW_sph_ll}).subs(R,R_FLRW_sph_).applyfunc(simplify)
display(Math('G_{\\mu \\nu}' + '=' + latex(Einstein_FLRW_sph_ll)))

In [ ]:
# Raise the first index
Einstein_FLRW_sph_ul=Einstein(st0,-st1).replace_with_arrays({Einstein(-st0,-st1):Einstein_FLRW_sph_ll, ST:metric_FLRW_sph_ll}, [st0,-st1]).applyfunc(lambda item:item.subs(a_to_Hubble).factor().expand())
display(Math('G^{\\mu}{}_{\\nu}' + '=' + latex(Einstein_FLRW_sph_ul)))

In [ ]:
# Matter energy-momentum
EMT_FLRW_sph_ll = ImmutableDenseNDimArray(Matrix([[rr(t), 0, 0, 0],[0,aa(t)**2*pp(t)/(1-k*r**2),0,0],[0,0,aa(t)**2*r**2*pp(t),0],[0,0,0,aa(t)**2*r**2*sin(theta)**2*pp(t)]]))
display(Math('T_{\\mu \\nu}' + '=' + latex(EMT_FLRW_sph_ll)))

In [ ]:
# Raise the first index
EMT_FLRW_sph_ul=EMT(st0,-st1).replace_with_arrays({EMT(-st0,-st1): EMT_FLRW_sph_ll, ST:metric_FLRW_sph_ll}, [st0,-st1])
display(Math('T^{\\mu}{}_{\\nu}' + '=' + latex(EMT_FLRW_sph_ul)))

In [ ]:
# Friedmann's equations for curved space
FR0k=Eq(-Einstein_FLRW_sph_ul[0,0],-coupling**2 * EMT_FLRW_sph_ul[0,0])
FR1k=Eq(-Einstein_FLRW_sph_ul[1,1],-coupling**2 * EMT_FLRW_sph_ul[1,1])
display(FR0k)
display(FR1k)

### Manipulate expressions

In [ ]:
# Combine these equations to get continuity equation
u,v = symbols('u, v', real=True)

CEqk=diff(FR0k.lhs-FR0k.rhs,t).subs(a_to_Hubble)+u*(FR1k.lhs-FR1k.rhs)+v*(FR0k.lhs-FR0k.rhs)
CEqk

In [ ]:
CEqk.expand().collect([diff(HH(t),t),aa(t)])

In [ ]:
CEq=CEqk.expand().subs(u,-3*HH(t)).subs(v,3*HH(t)).collect(HH(t),factor)
CEq

In [ ]:
# Express diff(rr(t),t)
solve(CEq,diff(rr(t),t))

In [ ]:
display(Math('\\dot{\\rho}=' + latex(solve(CEq,diff(rr(t),t))[0].factor())))

#### Exercise

Find the expression for acceleration

## Intermediate calculations (to be added)